In [1]:
import random
import time
# Two classes --> Player, Environment
# Player --> action(), totalReward,
# Environment --> displayBorad after action, curr_state, totalReward, each step reward,

class Player:
    def __init__(self):
        self.curr_state=0
        self.totalRewardReceived=0
        self.R = [-0.1,-0.1,-0.1,-0.1,1,-10,1,-0.1,10]
        self.P = [
            [0,0.25,0.25,0.25,0,0,0.25,0,0],
            [0.25,0,0.25,0,0.25,0,0,0.25,0],
            [0.25,0.25,0,0,0,0.25,0,0,0.25], 
            [0.25,0,0,0,0.25,0.25,0.25,0,0],
            [0,0.25,0,0.25,0,0.25,0,0.25,0],
            [0,0,0.25,0.25,0.25,0,0,0,0.25],
            [0.25,0,0,0.25,0,0,0,0.25,0.25],
            [0,0.25,0,0,0.25,0,0.25,0,0.25],
            [0,0,0.25,0,0,0.25,0.25,0.25,0]]
        self.V = [0,0,0,0,0,0,0,0,0]
        
        self.Matrix = [
            [2,1,6,3],
            [0,2,7,4],
            [1,0,8,5],
            [5,4,0,6],
            [3,5,1,7],
            [4,3,2,8],
            [8,7,3,0],
            [6,8,4,1],
            [7,6,5,2]
        ]
        self.history = []
        self.count_of_states = [0,0,0,0,0,0,0,0,0]
        self.alpha = 0.05
        self.no_of_episodes = 0
        self.epsilon = 1
        self.gamma = 1
        
    def RL_Agent(self):
        # maintain visited states, rewards.
        # exploit using greedy policy with prob=0.4.
        # explore all possibility with prob=0.6/m.
        
        ## history stores the values (state, Gt, y)
        for i in range(len(self.history)):
            Gt = self.history[i][1]
            old_gamma = self.history[i][2]
            reward = self.R[self.curr_state]
            Gt += old_gamma*reward
            new_gamma = old_gamma*self.gamma
            self.history[i][1] = Gt
            self.history[i][2] = new_gamma
            
        self.history.append([self.curr_state, self.R[self.curr_state], self.gamma])
        
        do = random.choices(["exploit", "explore"],weights=[1-self.epsilon, self.epsilon])[0]
#         print(do)
        if (do=="exploit"):
            state_with_max_possible_rewards = []
            possible_states = self.Matrix[self.curr_state]
            values_of_possible_states = []
            max_value=-10000
            for i in possible_states:
                values_of_possible_states.append(self.V[i])
                if (self.V[i]>max_value):
                    max_value=self.V[i]
            for i in range(len(values_of_possible_states)):
                if (values_of_possible_states[i]==max_value):
                    state_with_max_possible_rewards.append(possible_states[i])
#             print(state_with_max_possible_rewards)
#             print(self.curr_state,possible_states, values_of_possible_states)
            choosen_state = random.choice(state_with_max_possible_rewards)
            action = self.Matrix[self.curr_state].index(choosen_state)
                    
        else: # do == "explore"
            choosen_state = random.choices(range(0,len(self.V)), weights=self.P[self.curr_state])[0]
            action = self.Matrix[self.curr_state].index(choosen_state)
        
        return action
    ## endgame to update policy according to given history we got
    def endgame(self):
        
        self.no_of_episodes+=1
        if (self.no_of_episodes<=500):
            pass
        else:
            self.epsilon = 1.0/(1+self.no_of_episodes-500)
        for i in range(len(self.history)):
            Gt = self.history[i][1]
            old_gamma = self.history[i][2]
            reward = self.R[self.curr_state]
            Gt += old_gamma*reward
            new_gamma = old_gamma*self.gamma
            self.history[i][1] = Gt
            self.history[i][2] = new_gamma
            
        self.history.append([self.curr_state, self.R[self.curr_state], self.gamma])
        
        ## updating value of V using every count policy.
        for i in self.history:
            state=i[0]
            Gt=i[1]
#             self.count_of_states[state]+=1
#             self.V[state]+=(1.0/self.count_of_states[state])*(Gt-self.V[state])
            self.V[state]=self.V[state]+(self.alpha)*(Gt-self.V[state])
        
        self.curr_state=0
        self.totalRewardReceived=0
        self.history=[]
    
    def action(self):
#         time.sleep(2)
        action = self.RL_Agent()
        return action

In [2]:
class Environment:
    def __init__(self):
        self.left = chr(129136) #left
        self.up = chr(129137) #up
        self.right = chr(129138) #right
        self.down = chr(129139) #down

        ## symbols to represent possible termination rewards
        self.endWithPositiveRewards = chr(128681) #termination with positive rewards 
        self.endWithNegativeRewards = chr(128163) #termination with negative rewards

        ## symbols to represent player and fish
        self.player = chr(128130) #player
        self.fish = chr(128031) #fish
        
        self.actions = [self.left, self.right, self.up, self.down]
        self.values = [self.player,0,0,0,self.fish,self.endWithNegativeRewards,self.fish,0,self.endWithPositiveRewards]
        
        ## for player
        self.totalRewardReceived = 0
        self.curr_state = 0
        self.e = 0
        

    def display3x3matrix(self):
        print(" ___ ___ ___ ")
        for i in range(3):
            for j in range(3):
                if (isinstance(self.values[3*i+j], int)):
                    print("|",3*i+j,end=" ")
                else:
                    print("|",end="")
                    print(self.values[3*i+j],end=" ")
            print("|")
            print("|___|___|___|")
            
    def newStateAfterAction(self, action):
#         steps_in_that_direction = 1/2.
        steps_in_that_direction=random.choice([1,2])
        self.values[self.curr_state]=0
        if (self.curr_state==0):
            if (action==0): ## left
                self.curr_state=3-steps_in_that_direction
            elif (action==1): ## right
                self.curr_state=steps_in_that_direction
            elif (action==2):## up
                self.curr_state=9-steps_in_that_direction*3
            else: ## down
                self.curr_state=steps_in_that_direction*3
        elif (self.curr_state==1):
            if (action==0): ## left
                self.curr_state=[0,2][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[2,0][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[7,4][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[4,7][steps_in_that_direction-1]
        elif (self.curr_state==2):
            if (action==0): ## left
                self.curr_state=[1,0][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[0,1][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[8,5][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[5,8][steps_in_that_direction-1]
        elif (self.curr_state==3):
            if (action==0): ## left
                self.curr_state=[5,4][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[4,5][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[0,6][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[6,0][steps_in_that_direction-1]   
        elif (self.curr_state==4):
            if (action==0): ## left
                self.curr_state=[3,5][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[5,3][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[1,7][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[7,1][steps_in_that_direction-1]
            self.values[4]=self.fish
        elif (self.curr_state==5):
            if (action==0): ## left
                self.curr_state=[4,3][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[3,4][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[2,8][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[8,2][steps_in_that_direction-1]
        elif (self.curr_state==6):
            if (action==0): ## left
                self.curr_state=[8,7][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[7,8][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[3,0][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[0,3][steps_in_that_direction-1]
            self.values[6]=self.fish
        elif (self.curr_state==7):
            if (action==0): ## left
                self.curr_state=[6,8][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[8,6][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[4,1][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[1,4][steps_in_that_direction-1]
        elif (self.curr_state==8):
            if (action==0): ## left
                self.curr_state=[7,6][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[6,7][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[5,2][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[2,5][steps_in_that_direction-1]
        if (self.curr_state==5):
            print("Player Died!!")
            self.totalRewardReceived-=10
            self.e=1
        elif (self.curr_state==8):
            print("Player reaches the destination!!")
            self.totalRewardReceived+=10
            self.e=1
        elif (self.curr_state==4 or self.curr_state==6):
            print("Player got a reward of '1' by getting", self.fish)
            self.totalRewardReceived+=1
        else:
            self.totalRewardReceived-=0.1
        self.values[self.curr_state]=self.player
        
    def start_game(self, Player):
        self.totalRewardReceived = 0
        self.e=0 ## Use to determine the end of the game
        self.curr_state=0
        self.display3x3matrix()
        while(not self.e):
            print("Your Current Score", self.totalRewardReceived)
            print("You are currently at", self.curr_state, "position!")
            print("Possible actions to choose:", self.left, self.right, self.up, self.down)
#             time.sleep(2)
            action = Player.action()
            print("You have taken", self.actions[action],"action")
            self.newStateAfterAction(action)
            self.display3x3matrix()
            Player.totalRewardReceived=self.totalRewardReceived
            Player.curr_state = self.curr_state
        Player.endgame()
        self.values = [self.player,0,0,0,self.fish,self.endWithNegativeRewards,self.fish,0,self.endWithPositiveRewards]
        print("****************************Game Ends!!****************************")
        print("Your Final Score:", self.totalRewardReceived)
        print("****************************Game Ends!!****************************")
        return self.totalRewardReceived

In [3]:
player1 = Player()

In [4]:
environment = Environment()

In [5]:
reward=[]
for i in range(750):
    totalRewardReceived = environment.start_game(player1)
    reward.append(totalRewardReceived)

 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡰 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡰 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 1 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.30000000000000004
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.4
You are currently at 3 positio

You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡰 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 3.3
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡰 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |💂 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 4.3
You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 |💂 |🚩 |
|___|___|___|
Your Current Score 4.2
You are currently at 7 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
Player reaches the destination!!
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |💂 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: 14.2
*********************

|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.30000000000000004
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡰 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.4
You are currently at 1 position!
Possible ac

Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 |💂 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 7 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |💂 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0.8
You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0.7000000000000001
You are currently at 1 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0.6000000000000001
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
Player got a reward of '1' by ge

| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💂 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: -10.1
****************************Game Ends!!****************************
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 1
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0.9
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|_

...

|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 194.60000000000167
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 195.60000000000167
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 195.50000000000168
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 196.50000000000168
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___

You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 209.20000000000186
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 210.20000000000186
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 210.10000000000187
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 211.10000000000187
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 actio

| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 223.90000000000205
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 223.80000000000206
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 224.80000000000206
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 224.70000000000206
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|_

| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 237.40000000000225
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 237.30000000000226
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 237.20000000000226
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 237.10000000000227
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩

| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 |💂 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 7 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
Player reaches the destination!!
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |💂 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: 9.8
****************************Game Ends!!****************************
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡲 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
You have taken 🡱 action
Player Died!!
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💂 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___

In [6]:
totalRewardReceived

-10.1

In [7]:
player1.V

[5.535957925119727,
 7.778881080496931,
 -2.961017480142195,
 5.456830724849333,
 3.1720100300385314,
 -9.9999912738909,
 6.954405605356934,
 22.887468703510955,
 9.999999999775158]

In [8]:
max(reward)

423.9999999999926

In [9]:
player1.epsilon

0.00398406374501992